- Yousuf Ahmed
- CSCI 311 
- 10:45 AM Group 4 Project 1
- Mystery Prompts made by Yousuf Ahmed
- Solutions done by Fahim Tanvir

# Introduction: 

These are 7 queries we made to root out problems(a lot go whcih is related to theft or other nefarious schemes) one might find in a company or manager role.

Inspired by SQL NOIR

## Mystery 1
One of the employees committed commision fraud. It is proposed that they produced
a decent ammount of commissions and is one of the top 3 earning sales employees who made
a record sale.

**Step 1:**
Find all salespeople, and group from the highest sales of ALL sales orders.```

```

In [2]:
USE AdventureWorks2022;
GO

SELECT  p.FirstName + ' ' + p.LastName AS SalespersonName, 
    COUNT(soh.SalesOrderID) AS TotalOrdersCount
FROM   Person.Person AS p
JOIN Sales.SalesOrderHeader AS soh ON p.BusinessEntityID = soh.SalesPersonID 
WHERE  soh.SalesPersonID IS NOT NULL
GROUP BY p.FirstName, p.LastName
ORDER BY TotalOrdersCount DESC;

Commands completed successfully.

(17 rows affected)

Total execution time: 00:00:00.072

SalespersonName TotalOrdersCount Jillian Carson 473 Michael Blythe 450 Tsvi Reiter 429 Linda Mitchell 418 Jae Pak 348 José Saraiva 271 Shu Ito 242 Garrett Vargas 234 David Campbell 189 Ranjit Varkey Chudukatil 175 Tete Mensa-Annan 140 Rachel Valdez 130 Lynn Tsoflias 109 Pamela Ansman-Wolfe 95 Stephen Jiang 48 Amy Alberts 39 Syed Abbas 16

The top 3 for this one is Jillian Carson, Michael Blythe and Tsvi Reiter. 
This is a false herring as we should be looking for highest earners, not busiest person. 
We can make sure by checking how much they got through the actual profit they make

**Step 2**
Calculates the highest single sale value for every salesperson. This shortens our list of suspects


In [3]:
SELECT
    soh.SalesPersonID,
    p.FirstName,
    p.LastName,

MAX(soh.SubTotal) AS HighestSaleValue
FROM Sales.SalesOrderHeader AS soh
JOIN  Person.Person AS p ON soh.SalesPersonID = p.BusinessEntityID 
WHERE soh.SalesPersonID IS NOT NULL
GROUP BY soh.SalesPersonID, p.FirstName, p.LastName
ORDER BY HighestSaleValue DESC;

(17 rows affected)

Total execution time: 00:00:00.044

SalesPersonID FirstName LastName HighestSaleValue 281 Shu Ito 163930.3943 289 Jae Pak 150837.4387 290 Ranjit Varkey Chudukatil 147390.9328 275 Michael Blythe 146154.5653 276 Linda Mitchell 129261.254 279 Tsvi Reiter 126198.3362 277 Jillian Carson 117274.3453 282 José Saraiva 115310.4777 274 Stephen Jiang 112611.9697 283 David Campbell 109253.4254 284 Tete Mensa-Annan 106268.238 288 Rachel Valdez 104153.3951 280 Pamela Ansman-Wolfe 93591.6217 278 Garrett Vargas 85982.4771 287 Amy Alberts 71884.6078 286 Lynn Tsoflias 63669.48 285 Syed Abbas 57771.7641

OUTPUT: The top 3 for this one is Shu Ito, Jae Pak and Ranjit Varkey. 
We can make even more sure by seeing how much they made overall

**Step 3**
Finds the salesperson with the highest average sale value

In [4]:
SELECT 
    p.FirstName + ' ' + p.LastName AS SalesPersonName,  ReturnData.AverageOrderValue
FROM
    Person.Person AS p
JOIN (
    SELECT SalesPersonID,
    AVG(SubTotal) AS AverageOrderValue
    FROM Sales.SalesOrderHeader
    WHERE SalesPersonID IS NOT NULL
    GROUP BY SalesPersonID
) AS ReturnData ON p.BusinessEntityID = ReturnData.SalesPersonID
ORDER BY
    ReturnData.AverageOrderValue DESC; 

(17 rows affected)

Total execution time: 00:00:00.025

SalesPersonName AverageOrderValue Pamela Ansman-Wolfe 35001.0799 Shu Ito 26557.8741 Ranjit Varkey Chudukatil 25770.7938 Linda Mitchell 24801.4531 Jae Pak 24434.8811 Stephen Jiang 22752.5803 José Saraiva 21868.7024 Jillian Carson 21280.7685 Michael Blythe 20653.1177 David Campbell 19735.1605 Amy Alberts 18788.697 Tsvi Reiter 16715.6474 Tete Mensa-Annan 16518.1835 Garrett Vargas 15424.988 Rachel Valdez 14054.3593 Lynn Tsoflias 13044.1369 Syed Abbas 10782.7782

**OUTPUT AND MAIN CULPRIT**: Shu Ito is our main guy, he is 2nd highest earner

## Mystery 2
A customer is presumed to have shoplifted a lot of our merch. We know they frequented our 
store around the first week of october 2012 didn't spend that much overall. They weren't contacted 
a few months later from March to May due to them unsubscribing from our newsleter. 
They attempted to cover their trail by using legitamate purchases after May.

**Step 1** We gotta find the least spending customers

In [5]:
SELECT TOP 10 CustomerID, SUM(TotalDue) AS TotalSpent 
FROM Sales.SalesOrderHeader
WHERE OrderDate >= '2012-10-01' AND OrderDate <= '2012-10-07'
GROUP BY CustomerID
ORDER BY TotalSpent ASC;

(10 rows affected)

Total execution time: 00:00:00.027

CustomerID TotalSpent 15388 865.204 20598 865.204 20716 865.204 20859 865.204 26436 865.204 26439 865.204 26442 865.204 14239 1105.4834 14115 1105.4834 14112 1105.4834

**Step 2** 
Find customer that was contacted from May to March.
Find customers whose contact records were modified between March 1st and May 31st
WE MUST FIND SOMEONE WHO ISN'T PRESENT ON THE LIST

In [6]:
SELECT DISTINCT
    C.CustomerID,
    P.FirstName + ' ' + P.LastName AS CustomerName
FROM
    Sales.Customer AS C
JOIN
    Person.Person AS P ON C.PersonID = P.BusinessEntityID
WHERE
    C.PersonID IS NOT NULL
    AND (
        EXISTS (
            SELECT 1
            FROM Person.EmailAddress AS E
            WHERE E.BusinessEntityID = P.BusinessEntityID
            AND E.ModifiedDate >= '2012-03-01' AND E.ModifiedDate <= '2012-05-31'
        )
        OR
        EXISTS (
            SELECT 1
            FROM Person.PersonPhone AS PP
            WHERE PP.BusinessEntityID = P.BusinessEntityID
            AND PP.ModifiedDate >= '2012-03-01' AND PP.ModifiedDate <= '2012-05-31'
        )
   )
ORDER BY CustomerID;

(687 rows affected)

Total execution time: 00:00:00.176

CustomerID CustomerName 11246 Latasha Rubio 11249 Cindy Patel 11332 Deanna Ramos 11335 Carla Raman 11338 Frank Navarro 11380 Mitchell Kumar 11395 Beth Gutierrez 11412 Sydney Bryant 11421 Amy Sun 11423 Jasmine Stewart 11427 Desiree Dominguez 11428 Deanna Perez 11431 Bryant Garcia 11488 Jermaine Lopez 11489 Deborah Goel 11491 Andre Perez 11493 Dawn Wu 11494 Jimmy Gutierrez 11496 Gary Ortega 11548 Raymond Sanchez 11549 Crystal Liang 11654 Ariana Sanchez 11663 Seth Williams 11664 Alyssa Morgan 11665 Janet Dominguez 11666 Angel Baker 11671 Jessica Brown 11675 Devin Martinez 11678 Johnny Chavez 11683 Greg Taylor 11688 Victoria Morris 11690 Caroline Butler 11696 Mackenzie Campbell 11705 Brooke Richardson 11707 Natalie Cook 11708 Elizabeth Weisman 11727 Benjamin Taylor 11741 Tamara Chander 11742 Edward Lewis 11743 Chase Kelly 11745 Allison Gonzalez 11772 Cameron Moore 11773 Gavin Diaz 11774 Emma Sanchez 11775 Sierra Roberts 11776 Seth Mitchell 11777 Miranda Long 11778 Haley Henderson 11779 Sarah Jackson 11780 Jessica Alexander 11796 Isabel Jenkins 11797 Devin Coleman 11798 Brendan Chande 11799 Jessie Wang 11809 Juan Gray 11810 Antonio Washington 11811 Abigail Brooks 11812 Andrew Rodriguez 11813 Mary Patterson 11815 Hannah Patterson 11816 Joe Torres 11817 Morgan Miller 11818 Daniel Garcia 11825 Aimee She 11826 Jessie Alonso 11831 Christian Ross 11834 Fernando Flores 11837 Haley Alexander 11839 Tyler Brown 11854 Jason Mitchell 11872 Faith Patterson 11873 Ryan Zhang 11885 Kurt Sharma 11886 Katelyn Parker 11910 Jaclyn Zheng 11912 Rachael Sai 11914 Meagan Rana 11915 Philip Carlson 11916 Joe Rana 11917 Roy Sanz 11918 Kaylee Hill 11919 Warren Andersen 11920 Adrienne Gomez 11924 Ian Long 11925 Ashlee Jai 11929 Virginia Gonzalez 11930 Jaclyn Nara 11933 Mathew Rubio 11934 Justin Shan 11937 Devin Perez 11939 Kevin Washington 11942 George Gonzalez 11943 Dawn Huang 11944 Rachael Rodriguez 11945 Dennis Huang 11946 Brandy Saunders 11947 Jenny Zheng 11952 Dorothy Robinson 11954 Joseph Garcia 11955 Gabriel Green 11956 Alexandria Sandberg 11963 Antonio Patterson 11964 Sharon Salavaria 11967 Latasha Munoz 11968 Kelsey Becker 11969 Randy Xu 11976 Audrey Ramos 11977 Bonnie Jai 11983 Cheryl Ortega 11986 Max Alvarez 11988 Kathryn Chapman 11989 Kara Anand 11990 Joanna Vazquez 11991 Frederick Martinez 11992 Tonya Chande 11993 Rosa Wang 11994 Leah Hu 11995 Kelvin Carson 11996 Veronica Srini 11997 Kristina Kapoor 11998 Donna Sharma 11999 Johnny Shan 12000 Ashley Russell 12001 Shannon Yang 12002 Adriana Lopez 12003 Audrey Munoz 12004 Jarrod Suri 12005 Gilbert Shen 12007 Shannon Sun 12009 Ann Martinez 12010 Max Serrano 12011 Morgan Johnson 12013 Kayla Lewis 12014 Devin Sanders 12016 Meredith Serrano 12018 Devin Henderson 12021 Deborah Yuan 12023 Fernando Johnson 12025 Logan Diaz 12026 Lucas Flores 12027 Haley Wood 12030 Ana Washington 12033 Kristen Guo 12037 Patricia Chapman 12039 Ricardo Nath 12041 Seth Martin 12042 Alex Carter 12050 Aaron Young 12052 Makayla Ward 12053 Cedric Gao 12058 Chloe Nelson 12059 Jason Jenkins 12069 Garrett Kelly 12071 Robert Robinson 12072 Tristan Ross 12075 Cameron Griffin 12076 Chloe Washington 12078 Jose Edwards 12079 Nathaniel Cooper 12082 Lauren Sanchez 12083 Kayla Alexander 12084 Aidan Perry 12094 Bailey Bailey 12096 Caitlin Brooks 12102 Devin Simmons 12103 Chloe White 12104 Mariah Ross 12105 Abigail Foster 12108 James Walker 12109 Morgan Foster 12110 Bianca Guo 12112 Arianna Henderson 12116 Amanda Gray 12118 Miguel Sanchez 12120 Xavier Simmons 12121 Logan Wilson 12141 Kaitlyn Lee 12142 Gabriella Torres 12143 Logan Turner 12151 Steven Kelly 12152 Adrian Ramirez 12153 Kaitlyn Bailey 12155 Gabriella Lopez 12156 Bonnie Raji 12160 Jaclyn Zhang 12162 Luke Mitchell 12163 Aaron Wang 12164 Noah Butler 12167 Sebastian Stewart 12169 Abigail Howard 12170 Sara Reed 12171 Alyssa Cooper 12172 Eduardo Alexander 12173 Dalton Edwards 12174 Charles Phillips 12178 Ethan Shan 12179 Alexis Jones 12180 Holly Mehta 12181 Katelyn Sanders 12184 Isaiah Pe

Output: A lot of customers who responded to their emails

**Step 3** Find customer who isn't present on the list from step 2

In [7]:
SELECT DISTINCT
    C.CustomerID,
    P.FirstName + ' ' + P.LastName AS CustomerName
FROM
    Sales.Customer AS C
JOIN
    Person.Person AS P ON C.PersonID = P.BusinessEntityID
WHERE
    C.PersonID IS NOT NULL 
    AND NOT EXISTS (
        SELECT 1
        FROM Person.EmailAddress AS E
        WHERE E.BusinessEntityID = P.BusinessEntityID
        AND E.ModifiedDate >= '2012-03-01' AND E.ModifiedDate <= '2012-05-31'
    )
    AND NOT EXISTS (
        
        SELECT 1
        FROM Person.PersonPhone AS PP
        WHERE PP.BusinessEntityID = P.BusinessEntityID
        AND PP.ModifiedDate >= '2012-03-01' AND PP.ModifiedDate <= '2012-05-31'
    )
ORDER BY CustomerID;

(18432 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:00.207

CustomerID CustomerName 11000 Jon Yang 11001 Eugene Huang 11002 Ruben Torres 11003 Christy Zhu 11004 Elizabeth Johnson 11005 Julio Ruiz 11006 Janet Alvarez 11007 Marco Mehta 11008 Rob Verhoff 11009 Shannon Carlson 11010 Jacquelyn Suarez 11011 Curtis Lu 11012 Lauren Walker 11013 Ian Jenkins 11014 Sydney Bennett 11015 Chloe Young 11016 Wyatt Hill 11017 Shannon Wang 11018 Clarence Rai 11019 Luke Lal 11020 Jordan King 11021 Destiny Wilson 11022 Ethan Zhang 11023 Seth Edwards 11024 Russell Xie 11025 Alejandro Beck 11026 Harold Sai 11027 Jessie Zhao 11028 Jill Jimenez 11029 Jimmy Moreno 11030 Bethany Yuan 11031 Theresa Ramos 11032 Denise Stone 11033 Jaime Nath 11034 Ebony Gonzalez 11035 Wendy Dominguez 11036 Jennifer Russell 11037 Chloe Garcia 11038 Diana Hernandez 11039 Marc Martin 11040 Jesse Murphy 11041 Amanda Carter 11042 Megan Sanchez 11043 Nathan Simmons 11044 Adam Flores 11045 Leonard Nara 11046 Christine Yuan 11047 Jaclyn Lu 11048 Jeremy Powell 11049 Carol Rai 11050 Alan Zheng 11051 Daniel Johnson 11052 Heidi Lopez 11053 Ana Price 11054 Deanna Munoz 11055 Gilbert Raje 11056 Michele Nath 11057 Carl Andersen 11058 Marc Diaz 11059 Ashlee Andersen 11060 Jon Zhou 11061 Todd Gao 11062 Noah Powell 11063 Angela Murphy 11064 Chase Reed 11065 Jessica Henderson 11066 Grace Butler 11067 Caleb Carter 11068 Tiffany Liang 11069 Carolyn Navarro 11070 Willie Raji 11071 Linda Serrano 11072 Casey Luo 11073 Amy Ye 11074 Levi Arun 11075 Felicia Jimenez 11076 Blake Anderson 11077 Leah Ye 11078 Gina Martin 11079 Donald Gonzalez 11080 Damien Chander 11081 Savannah Baker 11082 Angela Butler 11083 Alyssa Cox 11084 Lucas Phillips 11085 Emily Johnson 11086 Ryan Brown 11087 Tamara Liang 11088 Hunter Davis 11089 Abigail Price 11090 Trevor Bryant 11091 Dalton Perez 11092 Cheryl Diaz 11093 Aimee He 11094 Cedric Ma 11095 Chad Kumar 11096 Andrés Anand 11097 Edwin Nara 11098 Mallory Rubio 11099 Adam Ross 11100 Latasha Navarro 11101 Abby Sai 11102 Julia Nelson 11103 Cassie Chande 11104 Edgar Sara 11105 Candace Fernandez 11106 Jessie Liu 11107 Bianca Lin 11108 Kari Alvarez 11109 Ruben Kapoor 11110 Curtis Yang 11111 Meredith Gutierrez 11112 Crystal Wang 11113 Micheal Blanco 11114 Leslie Moreno 11115 Alvin Cai 11116 Clinton Carlson 11117 April Deng 11118 Alvin Zeng 11119 Evan James 11120 Beth Jiménez 11121 Orlando Suarez 11122 Byron Vazquez 11123 Philip Alvarez 11124 Ross Jordan 11125 Dana Navarro 11126 Shaun Carson 11127 Jan Edwards 11128 Samantha Long 11129 Julia Wright 11130 Caroline Russell 11131 Amanda Rivera 11132 Melissa Richardson 11133 Angela Griffin 11134 Larry Townsend 11135 Marcus Harris 11136 Brianna Morgan 11137 Jasmine Taylor 11138 Lauren Davis 11139 Tanya Moreno 11140 Javier Alvarez 11141 Nicole Ramirez 11142 Eduardo Patterson 11143 Jonathan Henderson 11144 Edward Hernandez 11145 Jasmine Coleman 11146 Karla Goel 11147 Ernest Wu 11148 Ross Vazquez 11149 Theodore Gill 11150 Russell Shen 11151 Melinda Gill 11152 James Williams 11153 Angela James 11154 Megan Walker 11155 Hunter Robinson 11156 Maria Roberts 11157 Hannah Long 11158 Jason Wright 11159 Brianna Hughes 11160 Maurice Tang 11161 Emily Wood 11162 Chase Cox 11163 Gabriel Wang 11164 Devin Brooks 11165 Jocelyn Alexander 11166 Ashley Martinez 11167 Jasmine Barnes 11168 David Rodriguez 11169 Bryce Richardson 11170 Carol Howard 11171 Jonathan Hill 11172 Gabrielle Adams 11173 Sarah Thomas 11174 Nicholas Robinson 11175 Luis Wang 11176 Mason Roberts 11177 Jose Flores 11178 Nathan Johnson 11179 Molly Rodriguez 11180 April Anand 11181 Devin Martin 11182 Stephanie Torres 11183 Jasmine Lee 11184 Meghan Hernandez 11185 Ashley Henderson 11186 Sarah Price 11187 Jennifer Cooper 11188 Catherine Morris 11189 Lawrence Blanco 11190 Carson Bryant 11191 Kristi Perez 11192 James Brown 11193 Ian Gray 11194 Jacqueline Price 11195 Megan Henderson 11196 Alfredo Romero 11197 Andrea Morris 11198 Brooke Sanders 11199 Jacqueline Bennett 11200 Jason Griffin 11201 Amanda Foster 11202 Alexia Price 11203 Luis Diaz 11204 Destiny

OUTPUT: Customers that didn't respond in April, March or May 2012. 15388 
Or Victoria Smith is on that list!

**Step 4** Customers who bought something past May

In [8]:
SELECT DISTINCT
    C.CustomerID,
    P.FirstName + ' ' + P.LastName AS CustomerName
FROM
    Sales.Customer AS C
JOIN
    Person.Person AS P ON C.PersonID = P.BusinessEntityID
WHERE
    C.PersonID IS NOT NULL 
    AND C.CustomerID IN (
        SELECT DISTINCT CustomerID
        FROM Sales.SalesOrderHeader
        WHERE OrderDate > '2012-05-31'
    )
ORDER BY
    CustomerID;

(18801 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:00.217

CustomerID CustomerName 11000 Jon Yang 11001 Eugene Huang 11002 Ruben Torres 11003 Christy Zhu 11004 Elizabeth Johnson 11005 Julio Ruiz 11006 Janet Alvarez 11007 Marco Mehta 11008 Rob Verhoff 11009 Shannon Carlson 11010 Jacquelyn Suarez 11011 Curtis Lu 11012 Lauren Walker 11013 Ian Jenkins 11014 Sydney Bennett 11015 Chloe Young 11016 Wyatt Hill 11017 Shannon Wang 11018 Clarence Rai 11019 Luke Lal 11020 Jordan King 11021 Destiny Wilson 11022 Ethan Zhang 11023 Seth Edwards 11024 Russell Xie 11025 Alejandro Beck 11026 Harold Sai 11027 Jessie Zhao 11028 Jill Jimenez 11029 Jimmy Moreno 11030 Bethany Yuan 11031 Theresa Ramos 11032 Denise Stone 11033 Jaime Nath 11034 Ebony Gonzalez 11035 Wendy Dominguez 11036 Jennifer Russell 11037 Chloe Garcia 11038 Diana Hernandez 11039 Marc Martin 11040 Jesse Murphy 11041 Amanda Carter 11042 Megan Sanchez 11043 Nathan Simmons 11044 Adam Flores 11045 Leonard Nara 11046 Christine Yuan 11047 Jaclyn Lu 11048 Jeremy Powell 11049 Carol Rai 11050 Alan Zheng 11051 Daniel Johnson 11052 Heidi Lopez 11053 Ana Price 11054 Deanna Munoz 11055 Gilbert Raje 11056 Michele Nath 11057 Carl Andersen 11058 Marc Diaz 11059 Ashlee Andersen 11060 Jon Zhou 11061 Todd Gao 11062 Noah Powell 11063 Angela Murphy 11064 Chase Reed 11065 Jessica Henderson 11066 Grace Butler 11067 Caleb Carter 11068 Tiffany Liang 11069 Carolyn Navarro 11070 Willie Raji 11071 Linda Serrano 11072 Casey Luo 11073 Amy Ye 11074 Levi Arun 11075 Felicia Jimenez 11076 Blake Anderson 11077 Leah Ye 11078 Gina Martin 11079 Donald Gonzalez 11080 Damien Chander 11081 Savannah Baker 11082 Angela Butler 11083 Alyssa Cox 11084 Lucas Phillips 11085 Emily Johnson 11086 Ryan Brown 11087 Tamara Liang 11088 Hunter Davis 11089 Abigail Price 11090 Trevor Bryant 11091 Dalton Perez 11092 Cheryl Diaz 11093 Aimee He 11094 Cedric Ma 11095 Chad Kumar 11096 Andrés Anand 11097 Edwin Nara 11098 Mallory Rubio 11099 Adam Ross 11100 Latasha Navarro 11101 Abby Sai 11102 Julia Nelson 11103 Cassie Chande 11104 Edgar Sara 11105 Candace Fernandez 11106 Jessie Liu 11107 Bianca Lin 11108 Kari Alvarez 11109 Ruben Kapoor 11110 Curtis Yang 11111 Meredith Gutierrez 11112 Crystal Wang 11113 Micheal Blanco 11114 Leslie Moreno 11115 Alvin Cai 11116 Clinton Carlson 11117 April Deng 11118 Alvin Zeng 11119 Evan James 11120 Beth Jiménez 11121 Orlando Suarez 11122 Byron Vazquez 11123 Philip Alvarez 11124 Ross Jordan 11125 Dana Navarro 11126 Shaun Carson 11127 Jan Edwards 11128 Samantha Long 11129 Julia Wright 11130 Caroline Russell 11131 Amanda Rivera 11132 Melissa Richardson 11133 Angela Griffin 11134 Larry Townsend 11135 Marcus Harris 11136 Brianna Morgan 11137 Jasmine Taylor 11138 Lauren Davis 11139 Tanya Moreno 11140 Javier Alvarez 11141 Nicole Ramirez 11142 Eduardo Patterson 11143 Jonathan Henderson 11144 Edward Hernandez 11145 Jasmine Coleman 11146 Karla Goel 11147 Ernest Wu 11148 Ross Vazquez 11149 Theodore Gill 11150 Russell Shen 11151 Melinda Gill 11152 James Williams 11153 Angela James 11154 Megan Walker 11155 Hunter Robinson 11156 Maria Roberts 11157 Hannah Long 11158 Jason Wright 11159 Brianna Hughes 11160 Maurice Tang 11161 Emily Wood 11162 Chase Cox 11163 Gabriel Wang 11164 Devin Brooks 11165 Jocelyn Alexander 11166 Ashley Martinez 11167 Jasmine Barnes 11168 David Rodriguez 11169 Bryce Richardson 11170 Carol Howard 11171 Jonathan Hill 11172 Gabrielle Adams 11173 Sarah Thomas 11174 Nicholas Robinson 11175 Luis Wang 11176 Mason Roberts 11177 Jose Flores 11178 Nathan Johnson 11179 Molly Rodriguez 11180 April Anand 11181 Devin Martin 11182 Stephanie Torres 11183 Jasmine Lee 11184 Meghan Hernandez 11185 Ashley Henderson 11186 Sarah Price 11187 Jennifer Cooper 11188 Catherine Morris 11189 Lawrence Blanco 11190 Carson Bryant 11191 Kristi Perez 11192 James Brown 11193 Ian Gray 11194 Jacqueline Price 11195 Megan Henderson 11196 Alfredo Romero 11197 Andrea Morris 11198 Brooke Sanders 11199 Jacqueline Bennett 11200 Jason Griffin 11201 Amanda Foster 11202 Alexia Price 11203 Luis Diaz 11204 Destiny

OUTPUT AND MAIN CULPRIT:Victoria Smith did infact other something around a date after the month of 
 May. This fills our checkboxes

 ## Mystery 3
 A employee is sabotaging us by causing delays and losing profits by consistently smuggling
products to shipping facilities not authorized by us and is choosing cheap shipping
territories but  using expensive shipping methods.
They also have many high value sales despite this. How can we find this person?

**Step 1** Find the territory with lowest shipping cost

In [9]:
SELECT TOP 10 st.Name AS TerritoryName,
AVG(soh.Freight) AS AvgFreightCost
FROM
    Sales.SalesOrderHeader AS soh
JOIN
    Sales.SalesTerritory AS st ON soh.TerritoryID = st.TerritoryID
GROUP BY
    st.Name
ORDER BY
    AvgFreightCost ASC;

(10 rows affected)

Total execution time: 00:00:00.054

TerritoryName AvgFreightCost Australia 40.3276 Germany 51.2328 United Kingdom 66.8151 France 77.3625 Northwest 102.4482 Southwest 113.4619 Canada 119.613 Southeast 492.0851 Northeast 595.8029 Central 621.0824

**Step 2** Find seller who has most number of orders using most pricey shipping methods

In [10]:
WITH ExpensiveShippers AS (
    SELECT TOP 5
        ShipMethodID
    FROM
        Purchasing.ShipMethod
    ORDER BY
        ShipBase DESC
)
SELECT
    p.FirstName + ' ' + p.LastName AS EmployeeName,
    COUNT(soh.SalesOrderID) AS OrdersWithExpensiveShipping,
    AVG(soh.SubTotal) AS AvgSubtotalForExpensiveOrders
FROM
    Sales.SalesOrderHeader AS soh
JOIN
    Person.Person AS p ON soh.SalesPersonID = p.BusinessEntityID
WHERE
    soh.ShipMethodID IN (SELECT ShipMethodID FROM ExpensiveShippers)
    AND soh.SalesPersonID IS NOT NULL
GROUP BY
    p.FirstName, p.LastName
ORDER BY
    OrdersWithExpensiveShipping DESC;

(17 rows affected)

Total execution time: 00:00:00.074

EmployeeName OrdersWithExpensiveShipping AvgSubtotalForExpensiveOrders Jillian Carson 473 21280.7685 Michael Blythe 450 20653.1177 Tsvi Reiter 429 16715.6474 Linda Mitchell 418 24801.4531 Jae Pak 348 24434.8811 José Saraiva 271 21868.7024 Shu Ito 242 26557.8741 Garrett Vargas 234 15424.988 David Campbell 189 19735.1605 Ranjit Varkey Chudukatil 175 25770.7938 Tete Mensa-Annan 140 16518.1835 Rachel Valdez 130 14054.3593 Lynn Tsoflias 109 13044.1369 Pamela Ansman-Wolfe 95 35001.0799 Stephen Jiang 48 22752.5803 Amy Alberts 39 18788.697 Syed Abbas 16 10782.7782

**Step 3** Find who has the highest average ratio of Shipping Cost (Freight) to SubTotal,
indicating they are incurring high costs on low-value sales

In [11]:
SELECT TOP 1
    p.FirstName + ' ' + p.LastName AS SuspectName,
    AVG(soh.Freight / soh.SubTotal) AS AvgCostToValueRatio
FROM
    Sales.SalesOrderHeader AS soh
JOIN
    Person.Person AS p ON soh.SalesPersonID = p.BusinessEntityID
GROUP BY p.FirstName, p.LastName
ORDER BY AvgCostToValueRatio DESC;

(1 row affected)

Total execution time: 00:00:00.042

SuspectName AvgCostToValueRatio Lynn Tsoflias 0.031

**Step 4** Verify our suspect with location they ship in

In [12]:
SELECT
    p.FirstName + ' ' + p.LastName AS SalespersonName,
    st.Name AS TerritoryName
FROM
    Person.Person AS p
JOIN
    Sales.SalesPerson AS sp ON p.BusinessEntityID = sp.BusinessEntityID
JOIN
    Sales.SalesTerritory AS st ON sp.TerritoryID = st.TerritoryID
WHERE
    p.FirstName = 'Lynn' AND p.LastName = 'Tsoflias';

(1 row affected)

Total execution time: 00:00:00.023

SalespersonName TerritoryName Lynn Tsoflias Australia

Main output:Lynn Tsoflias ships in Australian territories or the cheapest shipping area. She is out culprit

## Mystery 4
An employee stole diamonds and placed them within purchases. This was discovered in  the last week
of December 2013 but could've happened earlier.It is a low selling item during that month, 
most likely for an accomplice to buy and  split the cost with the suspect. Who is that employee?
Who is that customer?

**Step 1** Identify the lowest selling product by volume in the  month of december

In [13]:
SELECT TOP 1 sod.ProductID,  p.Name AS ConcealmentProductName,
 SUM(sod.OrderQty) AS TotalQuantitySold
FROM
Sales.SalesOrderDetail AS sod 
JOIN
Sales.SalesOrderHeader AS soh ON sod.SalesOrderID = soh.SalesOrderID
JOIN
 Production.Product AS p ON sod.ProductID = p.ProductID
WHERE
    soh.OrderDate >= '2013-12-01'
    AND soh.OrderDate <= '2013-12-31'
GROUP BY sod.ProductID, p.Name
ORDER BY TotalQuantitySold ASC;

(1 row affected)

Total execution time: 00:00:00.054

ProductID ConcealmentProductName TotalQuantitySold 770 Road-650 Black, 52 1

Output is Road-650 Black, 52 with ProductID 770 and sold only once, helping us narrow thingds down

**Step 2** Find employee who sold it

In [14]:
SELECT TOP 1
    P.FirstName + ' ' + P.LastName AS SalespersonName,
    CAST(SOH.OrderDate AS DATE) AS SaleDate,
    sales.SalesOrderID
FROM Sales.SalesOrderDetail AS sales
JOIN  Sales.SalesOrderHeader AS SOH ON sales.SalesOrderID = SOH.SalesOrderID
JOIN Person.Person AS P ON SOH.SalesPersonID = P.BusinessEntityID
WHERE sales.ProductID = 770
ORDER BY SOH.OrderDate DESC;

(1 row affected)

Total execution time: 00:00:00.050

SalespersonName SaleDate SalesOrderID Rachel Valdez 2013-12-31 63166

OUTPUT AND MAIN CULPRIT: Rachel Valdes sold the item in 2013-12-31

**Step 3** Find customer associated with the sale

In [15]:
SELECT TOP 1
    P_Cust.FirstName + ' ' + P_Cust.LastName AS CustomerName,
    SOH.CustomerID,
    CAST(SOH.OrderDate AS DATE) AS SaleDate,
    sales.ProductID
FROM Sales.SalesOrderDetail AS sales
JOIN Sales.SalesOrderHeader AS SOH ON sales.SalesOrderID = SOH.SalesOrderID
JOIN Sales.Customer AS C ON SOH.CustomerID = C.CustomerID
JOIN Person.Person AS P_Cust ON C.PersonID = P_Cust.BusinessEntityID
WHERE sales.ProductID = 770
ORDER BY SOH.OrderDate DESC;

(1 row affected)

Total execution time: 00:00:00.043

CustomerName CustomerID SaleDate ProductID David Brink 29586 2013-12-31 770

OUTPUT AND ACCOMPLICE: David Brink is our main accomplice as he bought the item on the same day

## Mystery 5
An employee was victim to a phishing email. It is known that they clicked on the email on the year 2013,
when the system has updated their email, and the email was promising a promotion, which gets us to believe
it was low earning. 6 accounts were compromised including the original person who was sent the phising email. Who is this?

**Step 1** Find the date with the highest total number of contact record changes

In [16]:
SELECT TOP 1
    CAST(ModifiedDate AS DATE) AS BusiestUpdateDay,
    COUNT(BusinessEntityID) AS TotalContactUpdates
FROM
    Person.EmailAddress
GROUP BY
    CAST(ModifiedDate AS DATE)
ORDER BY
    TotalContactUpdates DESC;

(1 row affected)

Total execution time: 00:00:00.033

BusiestUpdateDay TotalContactUpdates 2013-07-31 136

**Step 2** Find the Top 10 Employees with the most recent contact modification dates in 2013

In [17]:
WITH UPDATED AS (
    SELECT BusinessEntityID, ModifiedDate FROM Person.EmailAddress WHERE YEAR(ModifiedDate) = 2013
    UNION ALL
    SELECT BusinessEntityID, ModifiedDate FROM Person.PersonPhone WHERE YEAR(ModifiedDate) = 2013
)
SELECT TOP 6 P.FirstName + ' ' + P.LastName as FullName, MAX(UPDATED.ModifiedDate) AS Datelastmodified
FROM UPDATED JOIN Person.Person AS P ON UPDATED.BusinessEntityID = P.BusinessEntityID
JOIN HumanResources.Employee AS HRE ON P.BusinessEntityID = HRE.BusinessEntityID
GROUP BY P.BusinessEntityID, P.FirstName, P.LastName
ORDER BY MAX(UPDATED.ModifiedDate) DESC;


(6 rows affected)

Total execution time: 00:00:00.089

FullName Datelastmodified Taylor Maxwell 2013-12-31 00:00:00.000 Jossef Goldberg 2013-12-16 00:00:00.000 Barry Johnson 2013-11-29 00:00:00.000 Rachel Valdez 2013-05-23 00:00:00.000 Lynn Tsoflias 2013-05-23 00:00:00.000 Syed Abbas 2013-03-07 00:00:00.000

**Step 3** Find lowest ranking Employee who had a recent contact modification from step 2

In [18]:
WITH LatestEmployeeContact AS (
    SELECT T.BusinessEntityID, MAX(T.ModifiedDate) AS LatestDate FROM (
        SELECT BusinessEntityID, ModifiedDate FROM Person.EmailAddress
        UNION ALL
        SELECT BusinessEntityID, ModifiedDate FROM Person.PersonPhone
    ) AS T GROUP BY T.BusinessEntityID
)
SELECT TOP 1 
    P.FirstName + ' ' + P.LastName AS Suspect, SP.SalesYTD, LEC.LatestDate
FROM LatestEmployeeContact AS LEC 
JOIN Sales.SalesPerson AS SP ON LEC.BusinessEntityID = SP.BusinessEntityID
JOIN Person.Person AS P ON LEC.BusinessEntityID = P.BusinessEntityID
ORDER BY  SP.SalesYTD ASC, LEC.LatestDate DESC;


(1 row affected)

Total execution time: 00:00:00.030

Suspect SalesYTD LatestDate Syed Abbas 172524.4512 2013-03-07 00:00:00.000

OUTPUT AND MAIN VICTIM is SYED Abbas

## Mystery 6
A product seems to vanish from stock. We sold some, but it doesn’t show up in recent orders. 
Let’s track when it was last sold and who sold it.

**Step 1** Find total sales of each product that have sold the least

In [19]:
SELECT TOP 5
    sod.ProductID,
    p.Name AS ProductName,
    SUM(sod.OrderQty) AS TotalSold
FROM Sales.SalesOrderDetail sod
JOIN Production.Product p ON sod.ProductID = p.ProductID
GROUP BY sod.ProductID, p.Name
ORDER BY TotalSold ASC;


(5 rows affected)

Total execution time: 00:00:00.067

ProductID ProductName TotalSold 897 LL Touring Frame - Blue, 58 4 942 ML Mountain Frame-W - Silver, 38 7 943 LL Mountain Frame - Black, 40 8 911 LL Road Seat/Saddle 10 898 LL Touring Frame - Blue, 62 15

**Step 2** Find who sold that product last

In [20]:
SELECT TOP 1
    soh.SalesPersonID,
    per.FirstName + ' ' + per.LastName AS Salesperson,
    soh.OrderDate,
    sod.ProductID
FROM Sales.SalesOrderHeader soh
JOIN Sales.SalesOrderDetail sod ON soh.SalesOrderID = sod.SalesOrderID
JOIN Person.Person per ON soh.SalesPersonID = per.BusinessEntityID
WHERE sod.ProductID = 897
ORDER BY soh.OrderDate DESC;

(1 row affected)

Total execution time: 00:00:00.065

SalesPersonID Salesperson OrderDate ProductID 282 José Saraiva 2013-06-30 00:00:00.000 897

OUTPUT AND CULPRIT: José Saraiva is the person who has sold the item last. The order was in 2013 which does not line up with the recent unlisted sales

## Mystery 7
An employee made up fake customers to hit bonus and commission targets. It is rumored this employe constantly creates new customers that order once and never again.

**Step 1** Figure out how many orders each customer has


In [21]:
SELECT 
    CustomerID,
    COUNT(SalesOrderID) AS OrdersCount
FROM Sales.SalesOrderHeader
GROUP BY CustomerID
ORDER BY OrdersCount ASC;

(19119 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:00.123

CustomerID OrdersCount 11020 1 11021 1 11022 1 11015 1 11016 1 11036 1 11037 1 11040 1 11041 1 11053 1 11062 1 11063 1 11064 1 11130 1 11135 1 11136 1 11144 1 11145 1 11132 1 11133 1 11140 1 11154 1 11155 1 11156 1 11162 1 11152 1 11158 1 11160 1 11248 1 11251 1 11265 1 11316 1 11342 1 11347 1 11348 1 11349 1 11350 1 11352 1 11354 1 11355 1 11373 1 11374 1 11375 1 11376 1 11377 1 11383 1 11384 1 11385 1 11386 1 11389 1 11390 1 11391 1 11392 1 11393 1 11399 1 11396 1 11397 1 11404 1 11405 1 11407 1 11408 1 11411 1 11415 1 11418 1 11424 1 11426 1 11430 1 11440 1 11441 1 11442 1 11435 1 11437 1 11438 1 11469 1 11471 1 11473 1 11474 1 11475 1 11476 1 11477 1 11478 1 11486 1 11487 1 11490 1 11495 1 11497 1 11509 1 11511 1 11512 1 11513 1 11514 1 11523 1 11526 1 11542 1 11543 1 11544 1 11545 1 11551 1 11552 1 11553 1 11554 1 11555 1 11556 1 11557 1 11558 1 11559 1 11560 1 11562 1 11563 1 11565 1 11569 1 11567 1 11573 1 11574 1 11579 1 11580 1 11584 1 11585 1 11586 1 11589 1 11594 1 11595 1 11596 1 11597 1 11600 1 11602 1 11608 1 11647 1 11693 1 11618 1 11888 1 11935 1 11936 1 12019 1 12020 1 12015 1 12017 1 12028 1 12029 1 12031 1 12032 1 12080 1 12081 1 12086 1 12090 1 12127 1 12223 1 12224 1 12227 1 12233 1 12234 1 12257 1 12258 1 12236 1 12238 1 12268 1 12269 1 12273 1 12274 1 12278 1 12312 1 12313 1 12322 1 12331 1 12368 1 12374 1 12375 1 12377 1 12379 1 12387 1 12389 1 12393 1 12396 1 12399 1 12400 1 12401 1 12405 1 12406 1 12407 1 12408 1 12415 1 12416 1 12417 1 12419 1 12420 1 12421 1 12422 1 12424 1 12425 1 12426 1 12427 1 12428 1 12429 1 12432 1 12433 1 12434 1 12403 1 12436 1 12439 1 12443 1 12445 1 12453 1 12454 1 12455 1 12456 1 12457 1 12458 1 12447 1 12449 1 12451 1 12469 1 12470 1 12471 1 12472 1 12466 1 12467 1 12477 1 12478 1 12481 1 12482 1 12488 1 12491 1 12493 1 12496 1 12497 1 12498 1 12514 1 12515 1 12516 1 12517 1 12518 1 12504 1 12505 1 12506 1 12507 1 12508 1 12511 1 12512 1 12524 1 12525 1 12527 1 12528 1 12529 1 12531 1 12541 1 12542 1 12543 1 12544 1 12534 1 12535 1 12536 1 12537 1 12538 1 12539 1 12555 1 12556 1 12557 1 12558 1 12569 1 12552 1 12553 1 12562 1 12565 1 12591 1 12600 1 12604 1 12605 1 12616 1 12617 1 12625 1 12628 1 12629 1 12635 1 12659 1 12660 1 12661 1 12662 1 12663 1 12641 1 12642 1 12639 1 12649 1 12651 1 12656 1 12714 1 12718 1 12719 1 12720 1 12721 1 12722 1 12723 1 12724 1 12725 1 12726 1 12727 1 12728 1 12716 1 12731 1 12732 1 12734 1 12737 1 12739 1 12741 1 12743 1 12744 1 12748 1 12751 1 12757 1 12758 1 12759 1 12763 1 12767 1 12765 1 12775 1 12781 1 12782 1 12783 1 12778 1 12785 1 12786 1 12790 1 12791 1 12792 1 12793 1 12794 1 12796 1 12797 1 12798 1 12799 1 12800 1 12801 1 12802 1 12809 1 12810 1 12811 1 12812 1 12814 1 12815 1 12818 1 12822 1 12823 1 12824 1 12788 1 12828 1 12831 1 12832 1 12835 1 12837 1 12838 1 12840 1 12842 1 12851 1 12847 1 12848 1 12844 1 12845 1 12862 1 12868 1 12869 1 12870 1 12875 1 12876 1 12877 1 12878 1 12879 1 12887 1 12888 1 12889 1 12890 1 12891 1 12872 1 12905 1 12906 1 12907 1 12908 1 12909 1 12910 1 12911 1 12896 1 12897 1 12899 1 12900 1 12902 1 12903 1 12914 1 12924 1 12925 1 12937 1 12938 1 12951 1 12952 1 12953 1 12946 1 12948 1 12965 1 12966 1 12967 1 12968 1 12971 1 12974 1 12976 1 12977 1 12978 1 12979 1 12983 1 13017 1 13027 1 13028 1 13030 1 13031 1 13033 1 13052 1 13053 1 13054 1 13061 1 13065 1 13073 1 13074 1 13084 1 13070 1 13094 1 13102 1 13097 1 13098 1 13100 1 13143 1 13145 1 13146 1 13147 1 13148 1 13151 1 13153 1 13154 1 13166 1 13167 1 13168 1 13162 1 13163 1 13164 1 13186 1 13187 1 13188 1 13191 1 13192 1 13193 1 13194 1 13195 1 13196 1 13200 1 13204 1 13207 1 13215 1 13216 1 13217 1 13218 1 13219 1 13209 1 13211 1 13223 1 13227 1 13228 1 13229 1 13213 1 13232 1 13234 1 13235 1 13236 1 13240 1 13241 1 13242 1 13244 1 13245 1 13266 1 13270 1 13271 1 13272 1 13275 1 13276 1 13281 1 13282 1 13293 1 13294 1 13295 1 13296 1 13297 1 13300 1 13301 1 13302 1 13305 1 13306 1 13307 1 13308 1 13309 1 13310 1 13311 1 13312 1 13313 1 1

**Step 2** Filter out the ID and Name of each customer that has only ordered once

In [22]:
SELECT 
    c.CustomerID,
    p.FirstName + ' ' + p.LastName AS CustomerName
FROM Sales.Customer c
JOIN Person.Person p ON c.PersonID = p.BusinessEntityID
WHERE c.CustomerID IN (
    SELECT CustomerID
    FROM Sales.SalesOrderHeader
    GROUP BY CustomerID
    HAVING COUNT(SalesOrderID) = 1
)
ORDER BY c.CustomerID;

(11649 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:00.143

CustomerID CustomerName 11015 Chloe Young 11016 Wyatt Hill 11020 Jordan King 11021 Destiny Wilson 11022 Ethan Zhang 11036 Jennifer Russell 11037 Chloe Garcia 11040 Jesse Murphy 11041 Amanda Carter 11053 Ana Price 11062 Noah Powell 11063 Angela Murphy 11064 Chase Reed 11130 Caroline Russell 11132 Melissa Richardson 11133 Angela Griffin 11135 Marcus Harris 11136 Brianna Morgan 11140 Javier Alvarez 11144 Edward Hernandez 11145 Jasmine Coleman 11152 James Williams 11154 Megan Walker 11155 Hunter Robinson 11156 Maria Roberts 11158 Jason Wright 11160 Maurice Tang 11162 Chase Cox 11248 Tristan Alexander 11251 Xavier Long 11265 Elizabeth Jones 11316 Luke Allen 11342 Marshall Wang 11347 Roy Navarro 11348 Shawn Rai 11349 Mindy Luo 11350 Cara Zhou 11352 Raymond Rodriguez 11354 Deanna Suarez 11355 Roberto Gutierrez 11373 Carly Luo 11374 Jimmy Ortega 11375 Francisco Martinez 11376 Lance Vazquez 11377 David Robinett 11383 Marie Gill 11384 Tiffany Wang 11385 Miguel Allen 11386 Jaclyn Cai 11389 Karl Shan 11390 Christine Raji 11391 Lindsay Xie 11392 Willie Zhao 11393 Kurt Pal 11396 Ian Lopez 11397 Latoya Shan 11399 Brenda Mehta 11404 Megan Taylor 11405 Bonnie Goel 11407 Mario She 11408 Darren Gill 11411 Devin Ross 11415 Randy She 11418 Rafael Hu 11424 Pamela Garcia 11426 Kristopher Mehta 11430 Casey Yuan 11435 Robin Romero 11437 Alfredo Moreno 11438 Jenny Nara 11440 Sergio Weber 11441 Erika Gomez 11442 Joseph Harris 11469 Edwin Raji 11471 Latasha Suarez 11473 Grace Henderson 11474 Melvin Xu 11475 Cesar Subram 11476 Erika Navarro 11477 Tristan Hughes 11478 Billy Hernandez 11486 Ariana Rogers 11487 Morgan Jones 11490 Danny Rubio 11495 Francis Jimenez 11497 Katrina Nath 11509 Roger Harui 11511 Caleb Perry 11512 Natalie Campbell 11513 Alyssa Howard 11514 Dalton Diaz 11523 Lucas Taylor 11526 Katherine Diaz 11542 Alejandro Tang 11543 Sheena Chande 11544 Joel Garcia 11545 Reginald Dominguez 11551 Shannon Alvarez 11552 Eddie Rubio 11553 Sharon Luo 11554 Sydney Simmons 11555 Alexandria Henderson 11556 Lucas Evans 11557 Felicia Ramos 11558 Ivan Malhotra 11559 Frederick Subram 11560 Whitney Srini 11562 Jarrod Gonzalez 11563 Cesar Srini 11565 Erik Diaz 11567 Carla Perez 11569 Troy Malhotra 11573 Meagan Subram 11574 Karla Luo 11579 Clayton Beck 11580 Melvin Raje 11584 Devin Carter 11585 Kari Perez 11586 Alberto Romero 11589 Ebony Malhotra 11594 Corey Goel 11595 Sebastian Howard 11596 Roger Raje 11597 Janelle Chandra 11600 Linda Rubio 11602 Larry Gill 11608 Cesar Madan 11618 Brian Ramirez 11647 Randy Wu 11693 Hailey Diaz 11888 Aaron Ross 11935 Jessica Taylor 11936 Hunter Clark 12015 Jacob White 12017 David Simmons 12019 Gabrielle Cox 12020 Olivia Rogers 12028 Sarah Lewis 12029 Damien Hu 12031 Logan Jai 12032 Tyler Taylor 12080 Grace Sanchez 12081 Kaitlyn Perez 12086 Emily Clark 12090 Savannah Carter 12127 Grace Davis 12223 Felicia Vazquez 12224 Tristan Henderson 12227 Kelsey Raje 12233 Jerry Yuan 12234 Clarence Zeng 12236 Kendra Gill 12238 Monica Raman 12257 Ross Ruiz 12258 Jamie Li 12268 Edwin Shan 12269 Warren Zheng 12273 Nelson Carlson 12274 Javier Torres 12278 Meredith Johnsen 12312 Jake Zhao 12313 Jaime Chande 12322 Kari Mehta 12331 Meagan Chandra 12368 Rodney Rubio 12374 Marie Kapoor 12375 Jarrod Raman 12377 Christopher Miller 12379 Bridget Chande 12387 Meredith Vazquez 12389 Albert Jiménez 12393 Brenda Sai 12396 Susan Yang 12399 Henry Chapman 12400 Andy Martin 12401 Kimberly Rivera 12403 Henry Young 12405 Cole Sanchez 12406 Ross Gutierrez 12407 Shawn Raji 12408 Jon Lu 12415 Brianna Richardson 12416 Veronica Martinez 12417 Alexis Bryant 12419 Destiny Bell 12420 Spencer Hayes 12421 Cameron Hughes 12422 Hailey Evans 12424 Rebecca Mitchell 12425 Brandon White 12426 Cody Cox 12427 Kimberly Stewart 12428 Sean Morris 12429 Melvin Black 12432 Nathan Clark 12433 Antonio Price 12434 Thomas Kumar 12436 Albert Diaz 12439 Megan Bennett 12443 Garrett James 12445 Cameron Taylor 12447 Carson Hayes 12449 Dylan Brown 12451 Anna Simmons 12453 Madison Bennett 12454 Samu

**Step 3** From the customers that have ordered once, figure out how many of those orders each employee placed

In [23]:
SELECT
    p.FirstName + ' ' + p.LastName AS Salesperson,
    COUNT(soh.SalesOrderID) AS OneTimeOrders
FROM Sales.SalesOrderHeader soh
JOIN Person.Person p ON soh.SalesPersonID = p.BusinessEntityID
WHERE soh.CustomerID IN (
    SELECT CustomerID
    FROM Sales.SalesOrderHeader
    GROUP BY CustomerID
    HAVING COUNT(SalesOrderID) = 1
)
GROUP BY p.FirstName, p.LastName
ORDER BY OneTimeOrders DESC;

(13 rows affected)

Total execution time: 00:00:00.052

Salesperson OneTimeOrders Tsvi Reiter 7 Linda Mitchell 4 Jillian Carson 3 Rachel Valdez 3 Garrett Vargas 2 Michael Blythe 2 David Campbell 2 Jae Pak 2 José Saraiva 1 Lynn Tsoflias 1 Shu Ito 1 Tete Mensa-Annan 1 Syed Abbas 1

Culprit: Tsvi Reiter has the most one time customer orders. It is a significant gap compared to other employees